This file shows how to upload the files, create the vector index or update it, then ask questions to the LLM

In [1]:
import os, json
import requests
from rich import print
from rich.pretty import pprint

In [2]:
data_dir = "data"  # data to play with inside notebooks 

In [3]:
filelist = [
    'ATT_SEC_AnnualReport_2022.pdf',
    'ATT_StockAnalystNote_Annual_20230125.pdf',
    'ATT_CompanyReport_Annual_20230126.pdf',
    'AMZN_MS_CompanyReport_Annual_20230203.pdf',
    'AMZN_Morning Star_StockAnalystNote_20230203.pdf',
    'AMZN_Moodys_CreditRating_2023.pdf',
    'AMZN_Morning Star_Transcript_Annual.pdf'
 ]

## Upload files

In [10]:
def upload_files(data_dir, filelist, url, show_content=False, n=2):
    if isinstance(filelist, str):
        filelist = [filelist]
    for filename in filelist[:n]:
        file_path = os.path.join(data_dir, filename)
        if os.path.isfile(file_path):
            with open(file_path, 'rb') as f:
                files = {'file': (filename, f)}
                response = requests.post(url, files=files)
                pprint(f"Uploaded {filename} with response {response.status_code}")
                if show_content:
                    pprint(json.loads(response.text))

In [7]:
!curl -X GET http://localhost:8003/ping/

{"answer":"78"}

In [40]:
# total wipe clean of files in 'data' and the vectorstore 
!curl -X DELETE http://localhost:8003/erase_data/
!curl -X DELETE http://localhost:8003/empty_collection/

{"message":"All data has been erased"}{"message":"Collection erased!"}

In [12]:
upload_url = 'http://localhost:8003/upload/'upload_url = 'http://localhost:8003/upload/'

upload_files(data_dir, filelist[1], upload_url, show_content=True)

'Uploaded ATT_StockAnalystNote_Annual_20230125.pdf with response 200'

{
│   'message': 'Successfully uploaded ATT_StockAnalystNote_Annual_20230125.pdf',
│   'ATT_StockAnalystNote_Annual_20230125.pdf': [
│   │   'Morningstar Equity Analyst Note | Report as of 25 Jan 2023 23:04, UTC | Reporting Currency: USD | Trading Currency: USD | Exchange: NEW YORK STOCK EXCHANGE, INC. Page 1 of 11\n©2023 Morningstar. All Rights Reserved. Unless otherwise provided in a separate agreement, you may use this report only in the country in which its original distributor is based. The information, data, analyses and \nopinions presented herein do not constitute investment advice; are provided solely for informational purposes and therefore are not an offer to buy or sell a security; and are not warranted to be correct, complete or \naccurate. The opinions expressed are as of the date written and are subject to change without notice. Except as otherwise required by law, Morningstar shall not be responsible for any trading decisions, damages or \nother losses resulting from, or related to, the information, data, analyses or opinions or their use. The information contained herein is the proprietary property of Morningstar and may not be reproduced, in whole or in \npart, or used in any manner, without the prior written consent of Morningstar. Investment research is produced and issued by subsidiaries of Morningstar, Inc. including, but not limited to, Morningstar Research \nServices LLC, registered with and governed by the U.S. Securities and Exchange Commission. To order reprints, call +1 312-696-6100. To license the research, call +1 312-696-6869. Please see important disclosures at \nthe end of this report.ß ®Financial Summary and Key Statistics \nActual Forecast\n2021 2022 2023 2024\nRevenue (USD Mil) 118,208 120,741 121,939 124,557\nRevenue Growth % 4.4 2.1 1.0 2.2\nOperating Income (Mil) 22,116 22,911 25,381 26,565\nOperating Margin % 18.7 19.0 20.8 21.3\nAdjusted EBITDA (Mil) 39,849 13,434 42,956 44,640\nAdjusted EBITDA Margin % 33.7 11.1 35.2 35.8\nEarnings Per Share (Diluted) (USD) 3.01 -1.15 2.59 2.63\nAdjusted Earnings Per Share (Diluted) (USD) 3.01 2.41 2.87 2.95\nAdjusted EPS Growth % 91.5 -19.8 18.8 2.8\nPrice/Earnings 6.2 7.6 7.1 6.9\nPrice/Book 1.8 1.4 1.4 1.2\nEV/EBITDA 9.4 26.5 6.7 6.4\nFree Cash Flow Yield % 12.4 9.2 11.5 13.0\nSource: Morningstar Valuation Model. Data as of 25 Jan 2023.AT&T Inc T QQQQ  25 Jan 2023 22:28, UTC\nLast Price Fair Value Estimate Price/FVE Market Cap Economic Moat TMMoat Trend TM Uncertainty Capital Allocation ESG Risk Rating Assessment 1\n20.42 USD\n25 Jan 202325.00 USD\n11 Apr 2022 03:30, UTC0.82136.57 USD Bil\n25 Jan 2023\nNarrow Stable Medium Poor ;;;;;\n4 Jan 2023 06:00, UTC\nMichael Hodel, CFA\nDirector\nMorningstar\n+1 (312) 696-6578\nmichael.hodel@morningstar.com\nContents\nAnalyst Note  (25 Jan 2023)\nBusiness Description\nFinancials\nResearch Methodology for Valuing \nCompanies\nImportant Disclosure\nThe conduct of Morningstar’s analysts is governed by Code of \nEthics/Code of Conduct Policy, Personal Security Trading Policy \n(or an equivalent of), and Investment Research Policy. For \ninformation regarding conflicts of interest, please visit: http://\nglobal.morningstar.com/equitydisclosures.\nThe primary analyst covering this company does not own its \nstock.\nReporting Currency: USD | Trading Currency: USD\nCurrency amounts expressed with "$" are in U.S. dollars \n(USD) unless otherwise denoted.\n1The ESG Risk Rating Assessment is a representation of \nSustainalytics’ ESG Risk Rating.Competitors Slowed AT&T During Fourth Quarter, but Growth \nRemains Solid \nAnalyst Note  Michael Hodel, CFA, Director, 25 Jan 2023\nAT&T isn’t attracting as many wireless customers as it was a year ago, but it continues to post solid results. \nCustomer retention was strong, but Verizon and T-Mobile seem to have effectively countered AT &T’s promotional \nefforts, which began in earnest about two years ago. Management expects wireless customer additions will \ndecline in 2023 as

In [8]:
!curl -X GET http://localhost:8003/list_files/

{"files":["ATT_StockAnalystNote_Annual_20230125.pdf"]}

In [15]:
# uploading files creates the embeddings in a parquet file
# when one is satisfied with the nb of files uploaded, he can create the index
# the parquet file is then destroyed to allow uploading files incrementally
!curl -X POST http://localhost:8003/create_index/

416.89s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


{"message":"Index creation successful"}

In [22]:
response = !curl -X POST http://localhost:8003/ask/ -H "Content-Type: application/json" -d '{"question": "Amazon 2024 forecast"}' 
pprint(json.loads(response[-1]))

{
│   'answer': [
│   │   'Amazon 2024 forecast is deemed RELEVANT with max score: 0.97',
│   │   '1: from ATT_StockAnalystNote_Annual_20230125.pdf - score:0.97 - 0 — — — — — — — — 0.0\nAdjusted EBITDA Growth % -21.9 43.8 -1.8 -66.3 219.8 3.9 4.2 4.6 5.0 30.6\nEarnings Per Share Growth % — — — — — — — — — 5.7\nAdjusted Earnings Per Share Growth % — — 91.5 -19.8 18.8 2.8 4.6 -1.3 4.4 5.7\nValuation as of 25 Jan 2023 Actual Forecast\n2020 2021 2022 2023 2024 2025 2026 2027\nPrice/Earnings 13.8 6.2 7.6 7.1 6.9 6.6 6.7 6.4\nPrice/Sales 2.5 1.7 1.5 1.1 1.1 1.1 1.0 1.0\nPrice/Book 1.0 1.8 1.4 1.4 1.',
│   │   '2: from ATT_StockAnalystNote_Annual_20230125.pdf - score:0.92 - 2 7.2 7.4 7.8 8.1 8.5\nForecast Revisions as of 25 Jan 2023 2023 2024 2025\nPrior data as of 20 Oct 2022 Current Prior Current Prior Current Prior\nFair Value Estimate Change (Trading Currency) 25.00 24.50 — — — —\nRevenue (USD Mil) 121,939 121,142 124,557 122,919 128,196 126,244\nOperating Income (USD Mil) 25,381 22,668 26,565 24,604 27,935 26,117\nEBITDA (USD Mil) 42,956 40,418 44,640 42,854 46,510 44,867\nNet Income (USD Mil) 20,651 19,073 21,231 20,359 22,197 21,530\nEarnings Per Share (Diluted) (USD) 2.59 2.37 2.63 2.51 2.72 2.',
│   │   '3: from ATT_StockAnalystNote_Annual_20230125.pdf - score:0.90 - 2 11.5 13.0 14.4 15.4 15.7\nOperating Performance / Profitability as of 25 Jan 2023 Actual Forecast\nFiscal Year, ends 31 Dec 2020 2021 2022 2023 2024 2025 2026 2027\nROA % 2.1 4.5 -2.1 4.6 4.5 4.5 4.4 4.5\nROE % 6.6 18.7 -10.7 19.1 17.4 16.3 15.0 14.4\nROIC % 4.7 5.8 -1.6 8.1 8.1 8.2 8.3 8.6',
│   │   '4: from ATT_StockAnalystNote_Annual_20230125.pdf - score:0.82 - Investment research is produced and issued by subsidiaries of Morningstar, Inc. including, but not limited to, Morningstar Research \nServices LLC, registered with and governed by the U.S. Securities and Exchange Commission. To order reprints, call +1 312-696-6100. To license the research, call +1 312-696-6869. Please see important disclosures at \nthe end of this report.ß ®Financial Summary and Key Statistics \nActual Forecast\n2021 2022 2023 2024\nRevenue (USD Mil) 118,208 120,741 121,939 124,557\nRevenue Growth % 4.4 2.1 1.0 2.2\nOperating Income (Mil) 22,116 22,911 25,381 26,565\nOperating Margin % 18.7 19.0 20.8 21.3\nAdjusted EBITDA (Mil) 39,849 13,434 42,956 44,640\nAdjusted EBITDA Margin % 33.7 11.1 35.2 35.',
│   │   '5: from ATT_StockAnalystNote_Annual_20230125.pdf - score:0.75 - 35 1.11 1.11 1.11 1.11 1.11\nMargins & Returns as of 25 Jan 2023 Actual Forecast\n3 Year Avg 2020 2021 2022 2023 2024 2025 2026 2027 5 Year Avg\nOperating Margin % 19.4 20.4 18.7 19.0 20.8 21.3 21.8 22.2 22.7 21.8\nEBITDA Margin % — 45.5 38.1 11.1 38.5 38.5 38.5 37.9 38.2 —\nAdjusted EBITDA Margin % 26.9 35.8 33.7 11.1 35.2 35.8 36.3 36.8 37.4 36.3\nNet Margin % 7.0 10.0 18.3 -7.2 15.3 15.2 15.3 14.9 15.1 15.2\nAdjusted Net Margin % 14.5 10.',
│   │   '6: from ATT_StockAnalystNote_Annual_20230125.pdf - score:0.69 - UTC\nFinancial Leverage (Reporting Currency) Actual Forecast\nFiscal Year, ends 31 Dec 2020 2021 2022 2023 2024 2025 2026 2027\nDebt/Capital % 49.3 70.0 58.3 55.3 53.6 51.2 48.8 47.2\nAssets/Equity 3.3 5.6 4.1 3.8 3.6 3.4 3.2 3.0\nNet Debt/EBITDA 2.8 3.5 9.6 2.7 2.6 2.4 2.3 2.1\nTotal Debt/EBITDA 3.9 4.4 10.1 3.1 3.1 2.9 2.8 2.7\nEBITDA/ Net Interest Expense 5.1 7.6 2.2 7.2 7.4 7.8 8.1 8.',
│   │   '7: from ATT_StockAnalystNote_Annual_20230125.pdf - score:0.67 - ends 31 Dec 2020 2021 2022 2023 2024 2025 2026 2027\nRevenue (USD Mil) 113,238 118,208 120,741 121,939 124,557 128,196 132,267 136,747\nOperating Income (USD Mil) 23,058 22,116 22,911 25,381 26,565 27,935 29,358 31,098\nEBITDA (USD Mil) 51,574 44,978 13,434 46,956 47,988 49,327 50,148 52,216\nAdjusted EBITDA (USD Mil) 40,570 39,849 13,434 42,956 44,640 46,510 48,633 51,073\nNet Income (USD Mil) 11,284 21,661 -8,727 18,641 18,917 19,558 19,651 20,697\nAdjusted Net Income (USD Mil) 11,284 21,661 18,311 20,651 21,231 22,',
│   │   '8: from ATT_Stock

In [ ]:
response = !curl -X POST "http://localhost:8003/ragit/"  -H "Content-Type: application/json" -d '{"question": "Amazon 2024 forecast?"}'

In [26]:
print(json.loads(response[-1])['answer'])

Based on the financial reports analyzed, the forecast for Amazon in 2024 is not provided in the context. The 
information retrieved from the search results pertains to different companies and their financial forecasts, such 
as revenue, operating income, EBITDA, net income, and various financial ratios. Therefore, the specific forecast 
for Amazon in 2024 is not available in the given context.

We see that despite high similarity scores, the vector search is completely off the mark because Amazon is not in the provided data at all.  I don't see how a vector search could overcome this situation.  But with one more step, RAG, I could instruct the model to look for relevance, and decide to answer or not.

Now, let's add a file with Amazon's financial report.

In [ ]:
upload_url = 'http://localhost:8003/upload/'
upload_files(data_dir, filelist[3], upload_url, show_content=True)
!curl -X POST http://localhost:8003/create_index/
response = !curl -X POST "http://localhost:8003/ask/"  -H "Content-Type: application/json" -d '{"question": "Amazon 2024 forecast?"}'

In [13]:
response = !curl -X POST "http://localhost:8003/ask/"  -H "Content-Type: application/json" -d '{"question": "Amazon 2024 forecast?"}'

We can see that Guardrails 'QA Relevance LLM Eval' doesn't work very well at all since it uses a LLM anyway, I prefer to use my own prompting (with ragit)

In [14]:
print(json.loads(response[-1])['answer'])

[
    'Amazon 2024 forecast? is deemed RELEVANT with max score: 0.83',
    '1: from AMZN_MS_CompanyReport_Annual_20230203.pdf - score:0.83 - IRRELEVANT answer -  Pii detected -Amazon’s 
first-quarter outlook \nincludes $121 billion to $126 billion in revenue and operating income from breakeven to 
$4.0 billion, compared \nwith FactSet consensus estimates of $125.5 billion and $4.0 billion, respectively. 
Guidance assumes 210 basis \npoints of pressure from currency impacts. Included in operating profit guidance is 
$640 million of severance \ncosts. which renders profitability guidance better than it appears at first glance. We 
see a path to continuous \nmargin improvement over time, even as uncertain macro conditions weigh in the near 
term.\nBusiness Strategy & Outlook  Dan Romanoff, Senior Equity Analyst, 3 Feb 2023\nAmazon dominates its served 
markets, notably e-commerce and cloud services. It benefits from numerous \ncompetitive advantages and has emerged 
as the clear e-commerce leader thanks to its size and scale, which \nyield an unmatched selection of low-priced 
goods for consumers.\n SUMMARY: <coroutine object summarize_it at 0x1f7d7c0b0>',
    '2: from AMZN_MS_CompanyReport_Annual_20230203.pdf - score:0.78 - RELEVANT answer -  Pii detected -Still, we 
\nsee shares as attractive.\n \nFourth-quarter revenue grew 9% year over year as reported, or 12% in constant 
currency, to $149.2 billion, \ncompared with guidance of $140 billion to $148 billion. Currency improved during the
quarter, which eased \npressure on revenue growth. Compared with our model, online stores was light, while 
third-party seller services \nwas well ahead, and other segments were in line to slightly ahead. From a retail 
perspective (all year over year, \nas reported), revenue from online stores declined 2%, physical stores improved 
6%, third-party seller services \ngrew 20%, and subscription services increased 13%. On the latter point, we’re 
impressed that Rings of Power \nhelped draw in new Prime members.\n \nThe two most critical segments, AWS and 
advertising, grew 20% and 19% over the year-ago period, respectively. \nManagement sees good customer additions 
within AWS and notes positive conversations about moving new \nFinancial Summary and Key Statistics \nActual 
Forecast\n2021 2022 2023 2024\nRevenue (USD Mil) 469,822 513,983 545,336 607,\n SUMMARY: <coroutine object 
summarize_it at 0x1f7c96dc0>',
    "3: from AMZN_MS_CompanyReport_Annual_20230203.pdf - score:0.76 - IRRELEVANT answer -  Pii detected 
-Pandemic-\nfueled growth last year in online stores and third-party seller services continued to slow to a 3% 
decline and 7% \ngrowth year over year in the quarter, respectively, while physical stores continue to benefit from
consumers \nleaving their homes to shop and grew by 17% year over year. Unit growth was flat, but we view this as a
mix \nissue as shopping habits normalize. Amazon noted no consumer slowdown as macro factors such as inflation and 
\nthe Russian invasion loom large. Compared with the year-ago period, subscription services slowed to 11% \ngrowth,
AWS posted strong 37% growth, and advertising decelerated to 23% growth. \nAmazon Delivers Mixed Quarter, Light 
Guidance, and Prime Price Hike; FVE Steady at $4,100  Dan \nRomanoff,Senior Equity Analyst,4 Feb 2022\nWe are 
maintaining our fair value estimate for wide-moat Amazon at $4,100 per share, and despite shares rising \n14% after
hours, we still view shares as undervalued. We think the highlight of the quarter was Amazon's plan to \nraise 
prices in the U.S.\n SUMMARY: <coroutine object summarize_it at 0x1f7d7c740>",
    "4: from AMZN_MS_CompanyReport_Annual_20230203.pdf - score:0.74 - IRRELEVANT answer -  Pii detected -In total, 
Amazon should grow at a 10% CAGR through 2027. We model GAAP operating margin \nexpanding from 2% (actual) in 2021 
to 6% in 2027 as the company grows into its expanded footprint and \noptimizes its substantial investment in 
transportati

In [20]:
filelist[3]

'AMZN_MS_CompanyReport_Annual_20230203.pdf'

In [12]:
upload_url = 'http://localhost:8003/upload/'
upload_files(data_dir, filelist[3], upload_url, show_content=True)
!curl -X POST http://localhost:8003/create_index/
response = !curl -X POST "http://localhost:8003/ragit/"  -H "Content-Type: application/json" -d '{"question": "Amazon 2024 forecast?"}'
print(json.loads(response[-1])['answer'])

'Uploaded AMZN_MS_CompanyReport_Annual_20230203.pdf with response 200'

{
│   'message': 'Successfully uploaded AMZN_MS_CompanyReport_Annual_20230203.pdf',
│   'AMZN_MS_CompanyReport_Annual_20230203.pdf': [
│   │   'Morningstar Equity Company Report | Report as of 3 Feb 2023 05:20, UTC | Reporting Currency: USD | Trading Currency: USD | Exchange: NASDAQ - ALL MARKETS Page 1 of 28\n©2023 Morningstar. All Rights Reserved. Unless otherwise provided in a separate agreement, you may use this report only in the country in which its original distributor is based. The information, data, analyses and \nopinions presented herein do not constitute investment advice; are provided solely for informational purposes and therefore are not an offer to buy or sell a security; and are not warranted to be correct, complete or \naccurate. The opinions expressed are as of the date written and are subject to change without notice. Except as otherwise required by law, Morningstar shall not be responsible for any trading decisions, damages or \nother losses resulting from, or related to, the information, data, analyses or opinions or their use. The information contained herein is the proprietary property of Morningstar and may not be reproduced, in whole or in \npart, or used in any manner, without the prior written consent of Morningstar. Investment research is produced and issued by subsidiaries of Morningstar, Inc. including, but not limited to, Morningstar Research \nServices LLC, registered with and governed by the U.S. Securities and Exchange Commission. To order reprints, call +1 312-696-6100. To license the research, call +1 312-696-6869. Please see important disclosures at \nthe end of this report.ß ®Amazon.com Inc AMZN QQQQ  3 Feb 2023 05:14, UTC\nLast Price Fair Value Estimate Price/FVE Market Cap Economic Moat TMMoat Trend TM Uncertainty Capital Allocation ESG Risk Rating Assessment 1\n112.91 USD\n2 Feb 2023137.00 USD\n3 Feb 2023 05:12, UTC0.821.07 USD Tril\n2 Feb 2023\nWide Stable High Exemplary ;;;;;\n1 Feb 2023 06:00, UTC\nDan Romanoff\nSenior Equity Analyst\nMorningstar\n+1 312 244 7816\ndan.romanoff@morningstar.com\nContents\nAnalyst Note  (3 Feb 2023)\nBusiness Description\nBusiness Strategy & Outlook  (3 Feb 2023)\nBulls Say / Bears Say  (3 Feb 2023)\nFair Value and Profit Drivers  (3 Feb 2023)\nEconomic Moat  (3 Jun 2022)\nMoat Trend  (3 Jun 2022)\nRisk and Uncertainty  (3 Jun 2022)\nFinancial Strength  (3 Feb 2023)\nCapital Allocation  (3 Feb 2023)\nFinancials\nRecent Analyst Notes\nResearch Methodology for Valuing \nCompanies\nImportant Disclosure\nThe conduct of Morningstar’s analysts is governed by Code of \nEthics/Code of Conduct Policy, Personal Security Trading Policy \n(or an equivalent of), and Investment Research Policy. For \ninformation regarding conflicts of interest, please visit: http://\nglobal.morningstar.com/equitydisclosures.\nThe primary analyst covering this company does not own its \nstock.\nReporting Currency: USD | Trading Currency: USD\nCurrency amounts expressed with "$" are in U.S. dollars \n(USD) unless otherwise denoted.\n1The ESG Risk Rating Assessment is a representation of \nSustainalytics’ ESG Risk Rating.Solid Results for Amazon With Continued AWS Deceleration in \nJanuary; Outlook Light; FVE Cut to $137\nAnalyst Note  Dan Romanoff, Senior Equity Analyst, 3 Feb 2023\nWide-moat Amazon reported solid fourth-quarter results, but provided a first-quarter outlook that was shy of our \nexpectations. E-commerce was generally solid while AWS continues to decelerate, including through January. \nWe see real progress being made on the operational side, which was masked by impairment charges. We still \nforesee healthy long-term growth driven by e-commerce proliferation, Amazon Web Services, or AWS, and \nadvertising, but the near term remains a work-in-progress with macro issues weighing on 2023, albeit with \nimprovement in 2024. We cut our estimates on both the top and bottom lines for 2023, while leaving the rest of \nour estimates largely unchanged. In turn, we cut our fair 

{"message":"Index creation successful"}

Amazon's 2024 forecast indicates a revenue projection of $607 billion. The company is expected to continue its 
growth trajectory, with a forecasted revenue increase from $513.9 billion in 2022 to $545.3 billion in 2023, and 
finally reaching $607 billion in 2024. Additionally, the forecast suggests an improvement in GAAP operating margin 
from 2% in 2021 to 6% in 2027, reflecting the company's efforts to optimize its investments and expand its 
operational efficiency.

### All files at once

In [16]:
# does not affect the vectorstore, but it will destroy the parquet file with the embeddings
# so make sure to create the index first
!curl -X DELETE http://localhost:8003/erase_data/

{"message":"All data has been erased"}

In [17]:
!curl -X DELETE http://localhost:8003/empty_collection/

{"message":"Collection erased!"}

In [23]:
upload_files(data_dir, filelist, upload_url, show_content=False, n=100)

'Uploaded ATT_SEC_AnnualReport_2022.pdf with response 200'

'Uploaded ATT_StockAnalystNote_Annual_20230125.pdf with response 200'

'Uploaded ATT_CompanyReport_Annual_20230126.pdf with response 200'

'Uploaded AMZN_MS_CompanyReport_Annual_20230203.pdf with response 200'

'Uploaded AMZN_Morning Star_StockAnalystNote_20230203.pdf with response 200'

'Uploaded AMZN_Moodys_CreditRating_2023.pdf with response 200'

'Uploaded AMZN_Morning Star_Transcript_Annual.pdf with response 200'

All files and their embeddings are now in the parquet file.  We can decide to push it into the vectorstore.  

In [24]:
!curl -X GET http://localhost:8003/list_files/

{"files":["ATT_SEC_AnnualReport_2022.pdf","text_vectors.parquet",".DS_Store","ATT_StockAnalystNote_Annual_20230125.pdf","ATT_CompanyReport_Annual_20230126.pdf","AMZN_MS_CompanyReport_Annual_20230203.pdf","AMZN_Morning Star_StockAnalystNote_20230203.pdf","AMZN_Moodys_CreditRating_2023.pdf","AMZN_Morning Star_Transcript_Annual.pdf"]}

In [25]:
# uploading files creates the embeddings in a parquet file
# when one is satisfied with the nb of files uploaded, he can create the index
# the parquet file is then destroyed to allow uploading files incrementally
!curl -X POST http://localhost:8003/create_index/

{"message":"Index creation successful"}

Now, we can ask questions

In [27]:
response = !curl -X POST "http://localhost:8003/ask/"  -H "Content-Type: application/json" -d '{"question": "Amazon 2024 forecast?"}'
print(json.loads(response[-1])['answer'])

[
    'Amazon 2024 forecast? is deemed RELEVANT with max score: 0.80',
    '1: from AMZN_MS_CompanyReport_Annual_20230203.pdf - score:0.80 - IRRELEVANT answer -  Pii detected -Amazon’s 
first-quarter outlook \nincludes $121 billion to $126 billion in revenue and operating income from breakeven to 
$4.0 billion, compared \nwith FactSet consensus estimates of $125.5 billion and $4.0 billion, respectively. 
Guidance assumes 210 basis \npoints of pressure from currency impacts. Included in operating profit guidance is 
$640 million of severance \ncosts. which renders profitability guidance better than it appears at first glance. We 
see a path to continuous \nmargin improvement over time, even as uncertain macro conditions weigh in the near 
term.\nBusiness Strategy & Outlook  Dan Romanoff, Senior Equity Analyst, 3 Feb 2023\nAmazon dominates its served 
markets, notably e-commerce and cloud services. It benefits from numerous \ncompetitive advantages and has emerged 
as the clear e-commerce leader thanks to its size and scale, which \nyield an unmatched selection of low-priced 
goods for consumers.\n SUMMARY: <coroutine object summarize_it at 0x1faaee5e0>',
    "2: from AMZN_Morning Star_Transcript_Annual.pdf - score:0.79 - IRRELEVANT answer -  Pii detected -Brian T. 
Olsavsky\nSenior Vice President and Chief Financial Officer | Amazon.com, Inc.\nHi, Mark. So, on the AWS growth 
rate, I'm not sure I can forecast for you with any level of certainty \nwhat is going to happen beyond this 
quarter. This is a bit uncharted territories economically. And \nas we mentioned, there's some unique things going 
on with the customer base. I think many in \nthis industry are all seeing the same thing. So, I don't have a 
crystal ball on that one, but we are \ngoing to continue to work for -- to be there for our customers. And as I 
said in the earlier \ncomments, we do have new deals. We have new workloads coming to the cloud. The value was 
\nthere, and whether there's short-term, perhaps short-term belt-tightening in the infrastructure \nexpense by a 
lot of companies, I think, the long-term trends are still there, and I think the quickest \nway to save money is to
get to the cloud, quite frankly.\nSo, there's a lot of long-term positive in tough economic times.\n SUMMARY: 
<coroutine object summarize_it at 0x1f79fbd80>",
    "3: from AMZN_Morning Star_Transcript_Annual.pdf - score:0.74 - IRRELEVANT answer -  Pii detected -beyond, but 
we hope to make -- expect to make big improvements in 2023.\nAndy Jassy\nPresident and Chief Executive Officer | 
Amazon.com, Inc.\nYeah. I'll start just at a broad level, priority wise, the connective tissue for everything we do
across \nthe Company, including in stores in North America is, we realize that we exist to make customers' \nlives 
better and easier every day, and relentlessly invent to do you so, and being maniacally \nfocused on the customer 
experience is always going to be a top priority for us. At the same time, \nand this is true in North America as 
well as across the entire business, we're working really hard \nto streamline our costs, and trying to do so, at 
the same time, that we don't give up on the long-\nterm strategic investments that we believe can meaningfully 
change broad customer experiences, \nand change Amazon over the long term.\n SUMMARY: <coroutine object 
summarize_it at 0x1f7bc28f0>",
    '4: from AMZN_Morning Star_StockAnalystNote_20230203.pdf - score:0.72 - IRRELEVANT answer -  Pii detected 
-Amazon continues to make progress on its excess expenses, particularly in improvements to the productivity of 
\nthe fulfillment network and transportation. Management plans to continue to optimize operations throughout 
\n2023.\nWhile guidance was slightly shy of our model, we are not surprised, given the macro environment. However, 
we \nthink the continued AWS deceleration in January will be unnerving to investors. Amazon’s first-quarter outlook
\nincludes $121 billion-$126 billi

In [28]:
response = !curl -X POST "http://localhost:8003/ragit/"  -H "Content-Type: application/json" -d '{"question": "Amazon 2024 forecast?"}'
print(json.loads(response[-1])['answer'])

Amazon's 2024 forecast is not explicitly provided in the given context. The information retrieved from the 
financial reports mainly focuses on Amazon's performance, outlook, and guidance for the first quarter of 2023, 
along with some insights into the company's long-term strategies and challenges. The reports discuss revenue, 
operating income, profitability guidance, market dominance in e-commerce and cloud services, cost optimization 
efforts, and the impact of various macroeconomic factors on Amazon's business.

Therefore, based on the provided context, there is no specific mention or projection related to Amazon's forecast 
for the year 2024.

In [14]:
!curl -X GET "https://jpbianchi-mr.hf.space/ping/"

{"answer":"3"}

In [12]:
!curl -X POST "https://jpbianchi-finrag.hf.space/ragit/"  -H "Content-Type: application/json" -d '{"question": "Does ATT have postpaid phone customers?"}'

{"answer":"Yes, AT&T does have postpaid phone customers. The company added 813,000 postpaid phone customers during the quarter, marking the strongest second quarter performance in a decade. Additionally, the average revenue per postpaid phone customer grew by 1.1% compared to the previous year, with further improvements expected in the second half."}

In [13]:
!curl -X POST "https://jpbianchi-finrag.hf.space/ragit/"  -H "Content-Type: application/json" -d '{"question": "what is Amazon loss?"}'

{"answer":"Amazon reported a pre-tax valuation loss of $2.3 billion in the fourth quarter, which was included in non-operating income from their common stock investment in Rivian Automotive. This loss was not related to Amazon's ongoing operations but rather stemmed from quarter-to-quarter fluctuations in Rivian's stock price."}